In [14]:
import pandas as pd
import streamlit as st
import numpy as np
import plotly.express as px
import altair as alt
import datetime
from scipy import stats
import vegafusion as vf

alt.data_transformers.enable("vegafusion")

DataTransformerRegistry.enable('vegafusion')

#US Vehicle Sales

In [15]:

df = pd.read_csv("vehicles_us.csv")
display(df.sample(n=5))
print(df.describe())
df.info()

price  model_year            model  condition  cylinders fuel  \
46848   5495      2009.0    nissan altima  excellent        4.0  gas   
8170    3700      1998.0     dodge dakota       good        6.0  gas   
11302   9995      2012.0     jeep liberty  excellent        NaN  gas   
33207  12905      2009.0  chevrolet tahoe       good        8.0  gas   
37585   6295      2014.0       ford focus  excellent        4.0  gas   

       odometer transmission    type paint_color  is_4wd date_posted  \
46848  123000.0    automatic   sedan         NaN     NaN  2018-09-11   
8170   203000.0    automatic  pickup       black     1.0  2019-03-12   
11302   59277.0    automatic     SUV       black     1.0  2019-03-26   
33207  118608.0    automatic     SUV      silver     NaN  2018-11-19   
37585  124000.0    automatic   sedan        grey     NaN  2018-06-12   

       days_listed  
46848           52  
8170            18  
11302           54  
33207           56  
37585           10

               price    model_year     cylinders       odometer   is_4wd  \
count   51525.000000  47906.000000  46265.000000   43633.000000  25572.0   
mean    12132.464920   2009.750470      6.125235  115553.461738      1.0   
std     10040.803015      6.282065      1.660360   65094.611341      0.0   
min         1.000000   1908.000000      3.000000       0.000000      1.0   
25%      5000.000000   2006.000000      4.000000   70000.000000      1.0   
50%      9000.000000   2011.000000      6.000000  113000.000000      1.0   
75%     16839.000000   2014.000000      8.000000  155000.000000      1.0   
max    375000.000000   2019.000000     12.000000  990000.000000      1.0   

       days_listed  
count  51525.00000  
mean      39.55476  
std       28.20427  
min        0.00000  
25%       19.00000  
50%       33.00000  
75%       53.00000  
max      271.00000  
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column      

***Checking for missing rows***


In [16]:
duplicates = df.duplicated().sum()
print(f"Number of duplicate rows: {duplicates}")


if duplicates > 0:
    duplicate_rows = df[df.duplicated()]
    print("Duplicate rows:")
    display(duplicate_rows)


Number of duplicate rows: 0


***Checking for missing values***
-  Columns with significant missing values: is_4wd, paint_color, odometer

In [17]:
df['is_4wd'] = df['is_4wd'].fillna(0)

missing_values_summary = df['is_4wd'].isnull().sum()
print(f"Missing values in 'is_4wd' after replacement: {missing_values_summary}")

df.to_csv('vehicles_us_cleaned.csv', index=False)


Missing values in 'is_4wd' after replacement: 0


-  I replaced the 'NaN' values in the 'is_4wd' column with '0' to ensure consistency in the dataset. A'NaN' value can complicate further, and '0' does not have an inherent vaule therefore will not scew the data

In [18]:
df['paint_color'] = df['paint_color'].fillna('unknown')

missing_values_summary = df['paint_color'].isnull().sum()
print(f"Missing values in 'paint_color' after replacement: {missing_values_summary}")

df.to_csv('vehicles_us_clearned.csv', index=False)

Missing values in 'paint_color' after replacement: 0


-  I replaced the 'NaN' values in the 'paint_color' column with 'unkown'. Missing values with 'NaN' could indicate that the paint color was not recorded in the dataset, but using 'unknown' is still dististive enough to maintain distinction between vehicles with missing paint color and those with specific pain colors

In [19]:
cylinder_mode = df['cylinders'].mode()[0]
print(f"Mode of cylinders: {cylinder_mode}")

df['cylinders'] = df['cylinders'].fillna(cylinder_mode)

missing_values_summary = df['cylinders'].isnull().sum()
print(f"Missing values in 'cylinders' after replacement: {missing_values_summary}")


Mode of cylinders: 8.0
Missing values in 'cylinders' after replacement: 0


In [20]:
odometer_median = df['odometer'].median()
print(f"Median of odometer: {odometer_median}")

df['odometer'] = df['odometer'].fillna(odometer_median)

missing_values_summary = df['odometer'].isnull().sum()
print(f"Missing values in 'odometer' after replacement: {missing_values_summary}")


Median of odometer: 113000.0
Missing values in 'odometer' after replacement: 0


In [21]:
model_year_median = df['model_year'].median()
print(f"Median of model_year: {model_year_median}")

df['model_year'] = df['model_year'].fillna(model_year_median)

missing_values_summary = df['model_year'].isnull().sum()
print(f"Missing values in 'model_year' after replacement: {missing_values_summary}")


Median of model_year: 2011.0
Missing values in 'model_year' after replacement: 0


In [22]:
display(df.sample(n=5))
df.info()

price  model_year                       model  condition  cylinders  \
32219  21499      2011.0          chevrolet traverse  excellent        6.0   
35769  17500      2006.0                    ram 3500       good        6.0   
49640  10995      2008.0                    acura tl       good        6.0   
20499   2999      2011.0            chevrolet malibu  excellent        4.0   
39774   9000      2011.0  chevrolet silverado 2500hd       good        8.0   

         fuel  odometer transmission   type paint_color  is_4wd date_posted  \
32219     gas   23500.0    automatic    SUV     unknown     0.0  2019-04-08   
35769  diesel  268500.0    automatic  truck       white     1.0  2018-12-25   
49640     gas   95150.0    automatic  sedan      silver     0.0  2019-04-06   
20499     gas  138000.0    automatic  sedan     unknown     0.0  2018-09-26   
39774     gas  201000.0    automatic  truck       white     1.0  2019-03-17   

       days_listed  
32219           42  
35769           21  
49640           58  
20499           81  
39774           17

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    51525 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     51525 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      51525 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   51525 non-null  object 
 10  is_4wd        51525 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [23]:
histogram = alt.Chart(df).mark_bar().encode(
    x=alt.X('price', bin=alt.Bin(maxbins=50), title='Price (USD)'),
    y=alt.Y('count()', title='Frequency')
).properties(
    title="Price Distribution of Vehicles"
)

scatterplot = alt.Chart(df).mark_circle(size=60).encode(
    x=alt.X('model_year:O', title='Model Year', axis=alt.Axis(labelAngle=-45)),  
    y=alt.Y('price', title='Price (USD)', scale=alt.Scale(zero=False)),  
    color=alt.Color('condition', title='Condition'),
    tooltip=['price', 'model_year', 'condition']
).properties(
    title="Scatterplot of Price vs Model Year",
    width=800,
    height=400
)

histogram.display()
scatterplot.display()

avg_price_by_condition = df.groupby('condition')['price'].mean().reset_index()

avg_price_by_condition.columns = ['Condition', 'Average Price']

print(avg_price_by_condition)


high_value_outliers = df[(df['price'] > 100000)]

high_value_outliers_with_model = high_value_outliers[['model_year', 'price', 'model', 'condition', 'type']]
display(high_value_outliers_with_model)


high_value_vehicles = df[df['price'] > 100000]

scatterplot_high_value = alt.Chart(high_value_vehicles).mark_circle(size=60).encode(
    x=alt.X('model:O', title='Model', axis=alt.Axis(labelAngle=-45)),  # Model type on the x-axis
    y=alt.Y('price', title='Price (USD)', scale=alt.Scale(domain=[100000, high_value_vehicles['price'].max()])),
    color=alt.Color('condition', title='Condition'),
    tooltip=['model', 'price', 'model_year', 'condition', 'type']
).properties(
    title="Vehicles Priced Over $100,000 by Model",
    width=1000, 
    height=400
)

scatterplot_high_value.display()


alt.Chart(...)

alt.Chart(...)

   Condition  Average Price
0  excellent   12806.669842
1       fair    3386.502178
2       good   10877.439067
3   like new   16677.445593
4        new   26050.300699
5    salvage    4242.295652


model_year   price                     model  condition    type
1309       2014.0  189000                ford f-150       good   truck
1668       2014.0  189000                ford f-150       good   truck
11359      2015.0  300000                  ram 2500  excellent   truck
12504      1999.0  375000           nissan frontier       good  pickup
20700      2011.0  109999        chevrolet corvette        new   coupe
22833      2012.0  115000     ford f-250 super duty       good   truck
24999      2004.0  140000                  ram 2500       good   truck
27375      2014.0  189000                ford f-150       good   truck
29810      2000.0  123456        chevrolet suburban       good   truck
30634      2014.0  189000                ford f-150       good   truck
33434      2014.0  189000                ford f-150       good   truck
34206      2004.0  175000         gmc sierra 2500hd       good   truck
34389      2014.0  189000                ford f-150       good   truck
36822      2000.0  123456        chevrolet suburban       good   truck
41748      2008.0  145000             toyota tundra   like new   truck
42853      2005.0  123456        chevrolet suburban       fair     SUV
45263      2006.0  120000  chevrolet silverado 1500       good   truck

alt.Chart(...)

***Price***
-  Less expensive cars sold more frequently
-  Condition of the car effected the cost 
- Trucks tended to be the most expensive vehicle with an exception to the Corvette 

In [24]:
fuel_trends = df.groupby(['model_year', 'fuel']).size().reset_index(name='Count')

chart = alt.Chart(fuel_trends).mark_line(point=True).encode(
    x=alt.X('model_year:O', title='Model Year', axis=alt.Axis(labelAngle=-45)), 
    y=alt.Y('Count', title='Count'),
    color=alt.Color('fuel', title='Fuel Type'),
    tooltip=['model_year', 'fuel', 'Count']
).properties(
    title='Trend of Fuel Types Over Model Years',
    width=800,
    height=400
)

chart.display()



alt.Chart(...)

***Fuel Types***
-  We see the popularity of gas increase until it's top popularity of 2011 and then a drastic decrease. Reason's for this could be due to the cost of gas, the increase of other options such as hybrid/electric options, and enviormental concerns

In [25]:
type_trends = df.groupby(['model_year', 'type']).size().reset_index(name='Count')

# Create the chart
chart = alt.Chart(type_trends).mark_line(point=True).encode(
    x=alt.X('model_year:O', title='Model Year', axis=alt.Axis(labelAngle=-45)),  # Treat model_year as ordinal for better readability
    y=alt.Y('Count', title='Count'),
    color=alt.Color('type', title='Vehicle Type'),
    tooltip=['model_year', 'type', 'Count']
).properties(
    title='Popularity of Vehicle Types Over Model Years',
    width=800,
    height=400
)

# Display the chart
chart.display()


alt.Chart(...)

***Vehicle Type Popularity***
-  We see the steady increase of all vehicle types over time with a higher uptick of trucks/pickups, SUVs, and sudans starting in the 90s with a quick drop off starting in 2011
-  Most car types have all seen a decline in sales as of 2017. This could be due to higher intrest rates/cost, cars lasting longer, and/or more opting for other means of transportation such as walking, biking, public transportation, or use of Uber/Lyft

In [26]:
chart = alt.Chart(df).mark_point().encode(
    x=alt.X('odometer', title='Odometer (miles)'),
    y=alt.Y('days_listed', title='Days Listed'),
    color=alt.Color('condition', title='Condition'), 

    tooltip=['odometer', 'days_listed', 'condition']
).properties(
    title='Scatter Plot: Days Listed vs Odometer',
    width=800,
    height=400
)

chart.display()


correlation = df[['odometer', 'days_listed']].corr()
print(correlation)


alt.Chart(...)

             odometer  days_listed
odometer     1.000000     0.003569
days_listed  0.003569     1.000000


***Days Listed***
-  Surprisingly miles on a vehicle does not effect the days listed as much which points to other factors being considered more